# エンドツーエンドのコードファースト生成AIエクスペリメント

このノートブックでは、DataRobotが提供する生成AI機能の包括的な概要を説明します。


**注**：セルフマネージドAIプラットフォームでは、`app.datarobot.com`を参照するコードサンプルは、インスタンスに適したURLに変更する必要があります。


In [ ]:
import datarobot as dr
from datarobot.models.genai.vector_database import VectorDatabase
from datarobot.models.genai.vector_database import ChunkingParameters
from datarobot.enums import PromptType
from datarobot.enums import VectorDatabaseEmbeddingModel
from datarobot.enums import VectorDatabaseChunkingMethod
from datarobot.models.genai.playground import Playground
from datarobot.models.genai.llm import LLMDefinition
from datarobot.models.genai.llm_blueprint import LLMBlueprint
from datarobot.models.genai.llm_blueprint import VectorDatabaseSettings
from datarobot.models.genai.chat import Chat
from datarobot.models.genai.chat_prompt import ChatPrompt
from datarobot.models.genai.vector_database import CustomModelVectorDatabaseValidation
from datarobot.models.genai.comparison_chat import ComparisonChat
from datarobot.models.genai.comparison_prompt import ComparisonPrompt
from datarobot.models.genai.custom_model_llm_validation import CustomModelLLMValidation

### DataRobotに接続する

[クライアントからDataRobotに接続する](https://docs.datarobot.com/ja/docs/api/api-quickstart/api-qs.html)ためのさまざまなオプションの詳細をご確認ください。


In [ ]:
endpoint="https://app.datarobot.com/api/v2"
token="<ADD_VALUE_HERE>"
dr.Client(endpoint=endpoint, token=token)

### ユースケースの作成

生成AIはDataRobotのユースケースの中で機能するので、新しいユースケースを作成することから始めます。


In [ ]:
use_case = dr.UseCase.create()

このワークフローでは、GenAIモデルでベクターデータベースを使用します。次に、一連のドキュメントを含むデータセットをアップロードします。


In [ ]:
# this can be updated with any public URL that is pointing to a .zip file
# in the expected format
dataset_url = "https://s3.amazonaws.com/datarobot_public_datasets/genai/pirate_resumes.zip"

# We will use a vector database with our GenAI models. Let's upload a dataset with our documents.
# If you wish to use a local file as dataset, change this to
# `dataset = dr.Dataset.create_from_file(local_file_path)`
dataset = dr.Dataset.create_from_url(dataset_url)

### ベクターデータベースの作成

In [ ]:
chunking_parameters = ChunkingParameters(
    embedding_model=VectorDatabaseEmbeddingModel.JINA_EMBEDDING_T_EN_V1,
    chunking_method=VectorDatabaseChunkingMethod.RECURSIVE,
    chunk_size=128,
    chunk_overlap_percentage=25,
    separators=[],
)
vdb = VectorDatabase.create(dataset.id, chunking_parameters, use_case)

以下のセルを使ってベクターデータベースを取得し、それが完了していることを確認します。

おおよその完了時間は30～60秒です。


In [ ]:
vdb = VectorDatabase.get(vdb.id)
assert vdb.execution_status == "COMPLETED"

### LLMプレイグラウンドの作成

大規模言語モデル（LLM）をホストするLLMプレイグラウンドを作成します。


In [ ]:
playground = Playground.create(name="New playground for example", use_case=use_case)

以下のセルを使って、使用可能なLLMの種類を確認します。デフォルトでは、このメソッドは読みやすいようにdictとして返します。これには、各LLMで使用できる設定のリストと、値に対する制約が含まれます。


In [ ]:
llms_dict = LLMDefinition.list(use_case=use_case)
print(llms_dict)

例として、GPT 3.5を使用します。


In [ ]:
llms = LLMDefinition.list(use_case=use_case, as_dict=False)
gpt = llms[0]

GPTと対話するには、希望の設定でLLMブループリントを作成する必要があります。使用できる設定はLLMのタイプによって異なるため、ブループリントの作成時に検証される値を含む一般的なdictを取ります。GPTで使用できる設定を確認します。


In [ ]:
print([setting.to_dict() for setting in gpt.settings])

### LLMブループリントの作成

In [ ]:
llm_settings = {
    "system_prompt": (
        "You are a pirate who begins each response with 'Arrr' "
        "and ends each response with 'Matey!'"
    ),
    "max_completion_length": 256,  # Let's ask for short responses
    "temperature": 2.0,  # With a high degree of variability
}
# PromptType.ONE_TIME_PROMPT is an alternative if you don't wish
# for previous chat prompts (history) to be included in each subsequent prompt
prompting_strategy = PromptType.CHAT_HISTORY_AWARE

データベース作成時のデフォルトとは異なるベクターデータベース設定を使用します。


In [ ]:
vector_database_settings = VectorDatabaseSettings(
    max_documents_retrieved_per_prompt=2,
    max_tokens=128,
)

llm_blueprint = LLMBlueprint.create(
    playground=playground,
    name="GPT",
    llm=gpt,
    prompt_type=prompting_strategy,
    llm_settings=llm_settings,
    vector_database=vdb,
    vector_database_settings=vector_database_settings,
)

### チャットの作成
次に、チャットを作成し、先の手順で作成したLLMブループリントに関連付けます。

チャットは、プロンプトメッセージのセットをグループ化するエンティティです。

これは、特定のLLMブループリントとの会話と考えることができます。


In [ ]:
chat = Chat.create(
    name="Resume review chat with a pirate",
    llm_blueprint=llm_blueprint
)

### LLMブループリントとのチャット

以下のセルを使って、LLMブループリントとチャットします。


In [ ]:
prompt1 = ChatPrompt.create(
    chat=chat,
    text="How can a pirate resume be evaluated?",
    wait_for_completion=True,
)
print(prompt1.result_text)

上のセル例は、`result_metadata`によって確認された、切り捨てられた出力を返します。


In [ ]:
print(prompt1.result_metadata.error_message)

`max_completion_length`を大きくして、もう一度チャットしてみます。LLM設定は、LLMブループリントがまだ保存されていない限り、チャットプロンプト内で更新できます。そうすることで、LLMブループリントの基本設定が更新されます。


In [ ]:
llm_settings["max_completion_length"] = 1024
prompt2 = ChatPrompt.create(
    text="Please answer the previous question again.",
    chat=chat,
    llm_settings=llm_settings,
    wait_for_completion=True,
)
print(prompt2.result_text)

新しい`max_completion_length`を維持して、LLMブループリントが更新されたことを確認できます。


In [ ]:
llm_blueprint = LLMBlueprint.get(llm_blueprint.id)
print(llm_blueprint.llm_settings)

回答が満足のいくものでないかもしれないため、次はTemperatureを下げて回答を修正します。


In [ ]:
llm_settings["temperature"] = 0.8
prompt3 = ChatPrompt.create(
    text="Please summarize the best pirate resume.",
    chat=chat,
    llm_settings=llm_settings,
    wait_for_completion=True,
)
print(prompt3.result_text)

LLMがベクターデータベースの情報を使用していることを確認します。


In [ ]:
print([citation.text for citation in prompt3.citations])

次に、既存のLLMブループリントから新しいLLMブループリントを作成し、いくつかの設定を変更して2つを比較します。


In [ ]:
new_llm_blueprint = LLMBlueprint.create_from_llm_blueprint(llm_blueprint, name="new blueprint")

新しいブループリントからベクターデータベースを削除し、以下のように設定を変更して、ブループリントを保存します。


In [ ]:
llm_settings["system_prompt"] = "You are an AI assistant who helps to evaluate resumes."
new_llm_blueprint = new_llm_blueprint.update(
    llm_settings=llm_settings,
    remove_vector_database=True,
)

ブループリントの設定が完了したら、UIで [LLMブループリントの比較](https://docs.datarobot.com/ja/docs/gen-ai/compare-llm.html)を実行するか、 [プレイグラウンドからデプロイ](https://docs.datarobot.com/en/docs/gen-ai/deploy-llm.html)することができます。



### 外部ベクターデータベースの追加

次に、デプロイから外部ベクターデータベースを追加します。

デプロイの作成は、この例では扱いません。

例のこの部分を続行するには、最初にここで外部ベクターデータベースデプロイの作成と検証を行い、`external_vdb_id`値を更新します。


最初に [このガイド](https://docs.datarobot.com/ja/docs/gen-ai/ext-vector-db.html)に従って、外部ベクターデータベースの作成とデプロイを行うことができます。


この作業が完了したら、ここで外部ベクターデータベースIDを更新して使用します。


In [ ]:
external_vdb_id = "<ADD_VALUE_HERE>"

In [ ]:
# Now create a vector database
external_model_vdb = VectorDatabase.get(
    vector_database_id=external_vdb_id
)
assert external_model_vdb.execution_status == "COMPLETED"

### 外部モデルLLMの追加

次に、デプロイから外部LLMブループリントを追加します。デプロイの作成はこの例の範囲外なので、以前にデプロイされたテキスト生成モデルを想定します。

例のこの部分を続行するには、最初にここで外部LLMデプロイの作成と検証を行い、`external_llm_validation_id`値を更新します。


最初に [このガイド](https://docs.datarobot.com/ja/docs/gen-ai/ext-llm.html)に従って、外部LLMの作成と検証を行うことができます。


この作業が完了したら、ここで外部LLMの検証IDを更新して使用します。


In [ ]:
external_llm_validation_id = "<ADD_VALUE_HERE>"

In [ ]:
external_llm_validation = CustomModelLLMValidation.get(validation_id=external_llm_validation_id)
assert external_llm_validation.validation_status == "PASSED"

カスタムモデルLLMとカスタムモデルベクターデータベースを使ってLLMブループリントを作成できるようになりました。


In [ ]:
custom_model_llm_blueprint = LLMBlueprint.create(
    playground=playground,
    name="custom model LLM with custom model vdb",
    llm="custom-model",
    llm_settings={
        "validation_id": external_llm_validation.id,
        # NOTE - update this value based on the context size in tokens
        # of the external LLM that you are deploying
        "external_llm_context_size": 4096
    },
    vector_database=external_model_vdb,
)

### 比較チャットの作成
最後に、`comparison_chat`を作成してプレイグラウンドに関連付けます。

比較チャットは、チャットプロンプトのチャットと同様に、比較プロンプトメッセージのセットをグループ化するエンティティです。

これは1つまたは複数のLLMブループリントとの会話と考えることができます。


In [ ]:
comparison_chat = ComparisonChat.create(
    name="Resume review comparison chat with a pirate",
    playground=playground
)

次に、LLMブループリントを比較します。

ドキュメントで設定されているので、`custom_model_llm_blueprint`の回答は、予期される著作権侵害の再開とは関係がありません。ユースケースに合わせて、外部VDBの作成や外部LLMを自由に変更できます。


In [ ]:
comparison_prompt = ComparisonPrompt.create(
    llm_blueprints=[llm_blueprint, new_llm_blueprint, custom_model_llm_blueprint],
    text="Summarize the best resume",
    comparison_chat=comparison_chat,    
    wait_for_completion=True,
)
print([result.result_text for result in comparison_prompt.results])